In [1]:
import numpy as np
import pandas as pd

pd.options.display.max_columns = 100

In [2]:

df_crop_details = pd.read_excel('./data/2.xlsx', sheet_name=1)

In [3]:
# 去除空格
df_crop_details['cropName'] = df_crop_details['cropName'].apply(lambda x: x.strip())


In [4]:
df_crop_planting = pd.read_excel('./data/2.xlsx', sheet_name=0)
# 照例去除一下空格
df_crop_planting['cropName'] = df_crop_planting['cropName'].apply(lambda x: x.strip())
# ffill
df_crop_planting['landName'] = df_crop_planting['landName'].ffill()

In [5]:
df_land = pd.read_excel('./data/1.xlsx', sheet_name=0)
# 去除landType和landName的空格
df_land['landType'] = df_land['landType'].apply(lambda x: x.strip())
df_land['landName'] = df_land['landName'].apply(lambda x: x.strip())

In [6]:
# 计算利润
unit_profit_lsc = []
for line in df_crop_details.values:
    s = str(line[7]).split('-')
    unit_profit_lsc.append((float(s[0]) + float(s[1])) / 2 * line[5] - line[6])
df_crop_details['unitProfit'] = unit_profit_lsc

In [7]:
df_crop_type_land = pd.read_excel('./data/1.xlsx', sheet_name=1)
# 老规矩，去掉cropName和cropType的空格
df_crop_type_land['cropType'] = df_crop_type_land['cropType'].apply(lambda x: x.strip())
df_crop_type_land['cropName'] = df_crop_type_land['cropName'].apply(lambda x: x.strip())

In [8]:
# 搞一下季节和年份的集合
SeasonType = ["单季", "第一季", "第二季"]
SeasonDict = {"单季": 1, "第一季": 1, "第二季": 2}
SeasonNum = [1, 2]
years = [2024, 2025, 2026, 2027, 2028, 2029, 2030]

In [9]:
# 枚举地块类型
LandType = {"A": "平旱地", "B": "梯田", "C": "山坡地", "D": "水浇地", "E": "普通大棚", "F": "智慧大棚"}

In [10]:
# 枚举地块
LandName = df_crop_planting['landName'].unique()

In [11]:
# 枚举地块面积，取df_land的landName为key，landArea为value
LandArea = {x: df_land[df_land['landName'] == x]['landArea'].values[0] for x in LandName}

In [12]:
# 读入作物名称
CropName = df_crop_details['cropName'].unique()

In [13]:
# 作物分类
CropType = {x: df_crop_type_land[df_crop_type_land['cropType'] == x]['cropName'].values for x in
            df_crop_type_land['cropType'].values}
CropType['粮食（除了水稻）'] = CropType['粮食'][:-1]  # 这样不太好，但能用
CropType['豆类'] = np.array(list(CropType['粮食（豆类）']) + list(CropType['蔬菜（豆类）']), dtype=object)
CropType['全粮食'] = np.array(list(CropType['粮食']) + list(CropType['粮食（豆类）']), dtype=object)
CropType['全粮食（除了水稻）'] = np.array(list(CropType['粮食'][:-1]) + list(CropType['粮食（豆类）']), dtype=object)
CropType['全蔬菜'] = np.array(list(CropType['蔬菜']) + list(CropType['蔬菜（豆类）']), dtype=object)
CropType['特殊蔬菜'] = np.array(["大白菜", "白萝卜", "红萝卜"], dtype=object)
CropType["普通蔬菜"] = np.array([c for c in CropType['全蔬菜'] if c not in CropType['特殊蔬菜']], dtype=object)
CropType

{'粮食（豆类）': array(['黄豆', '黑豆', '红豆', '绿豆', '爬豆'], dtype=object),
 '粮食': array(['小麦', '玉米', '谷子', '高粱', '黍子', '荞麦', '南瓜', '红薯', '莜麦', '大麦', '水稻'],
       dtype=object),
 '蔬菜（豆类）': array(['豇豆', '刀豆', '芸豆'], dtype=object),
 '蔬菜': array(['土豆', '西红柿', '茄子', '菠菜', '青椒', '菜花', '包菜', '油麦菜', '小青菜', '黄瓜',
        '生菜', '辣椒', '空心菜', '黄心菜', '芹菜', '大白菜', '白萝卜', '红萝卜'], dtype=object),
 '食用菌': array(['榆黄菇', '香菇', '白灵菇', '羊肚菌'], dtype=object),
 '粮食（除了水稻）': array(['小麦', '玉米', '谷子', '高粱', '黍子', '荞麦', '南瓜', '红薯', '莜麦', '大麦'],
       dtype=object),
 '豆类': array(['黄豆', '黑豆', '红豆', '绿豆', '爬豆', '豇豆', '刀豆', '芸豆'], dtype=object),
 '全粮食': array(['小麦', '玉米', '谷子', '高粱', '黍子', '荞麦', '南瓜', '红薯', '莜麦', '大麦', '水稻',
        '黄豆', '黑豆', '红豆', '绿豆', '爬豆'], dtype=object),
 '全粮食（除了水稻）': array(['小麦', '玉米', '谷子', '高粱', '黍子', '荞麦', '南瓜', '红薯', '莜麦', '大麦', '黄豆',
        '黑豆', '红豆', '绿豆', '爬豆'], dtype=object),
 '全蔬菜': array(['土豆', '西红柿', '茄子', '菠菜', '青椒', '菜花', '包菜', '油麦菜', '小青菜', '黄瓜',
        '生菜', '辣椒', '空心菜', '黄心菜', '芹菜', 

In [14]:
# 亩产量
unit_yield_lsc = {
    l: {
        1: {
            c: df_crop_details[
                (df_crop_details['cropName'] == c) &
                (df_crop_details['cropLandType'] == l) &
                ((df_crop_details['season'] == "单季") |
                 (df_crop_details['season'] == "第一季"))
                ]['unitYield'].values[0] if df_crop_details[
                                                (df_crop_details['cropName'] == c) &
                                                (df_crop_details['cropLandType'] == l) &
                                                ((df_crop_details['season'] == "单季") |
                                                 (df_crop_details['season'] == "第一季"))
                                                ]['unitYield'].values.size > 0 else 0
            for c in CropName
        },
        2: {
            c: df_crop_details[
                (df_crop_details['cropName'] == c) &
                (df_crop_details['cropLandType'] == l) &
                (df_crop_details['season'] == "第二季")
                ]['unitYield'].values[0] if df_crop_details[
                                                (df_crop_details['cropName'] == c) &
                                                (df_crop_details['cropLandType'] == l) &
                                                (df_crop_details['season'] == "第二季")][
                                                'unitYield'].values.size > 0 else 0
            for c in CropName
        }
    }
    for l in LandType.values()
}


In [15]:
# 亩利润
unit_profit_lsc = {
    l: {
        1: {
            c: df_crop_details[
                (df_crop_details['cropName'] == c) &
                (df_crop_details['cropLandType'] == l) &
                ((df_crop_details['season'] == "单季") |
                 (df_crop_details['season'] == "第一季"))
                ]['unitProfit'].values[0] if df_crop_details[
                                                 (df_crop_details['cropName'] == c) &
                                                 (df_crop_details['cropLandType'] == l) &
                                                 ((df_crop_details['season'] == "单季") |
                                                  (df_crop_details['season'] == "第一季"))
                                                 ]['unitProfit'].values.size > 0 else 0
            for c in CropName
        },
        2: {
            c: df_crop_details[
                (df_crop_details['cropName'] == c) &
                (df_crop_details['cropLandType'] == l) &
                (df_crop_details['season'] == "第二季")
                ]['unitProfit'].values[0] if df_crop_details[
                                                 (df_crop_details['cropName'] == c) &
                                                 (df_crop_details['cropLandType'] == l) &
                                                 (df_crop_details['season'] == "第二季")
                                                 ]['unitProfit'].values.size > 0 else 0
            for c in CropName
        }
    }
    for l in LandType.values()
}


In [16]:
# 亩成本
unit_cost_lsc = {
    l: {
        1: {
            c: df_crop_details[
                (df_crop_details['cropName'] == c) &
                (df_crop_details['cropLandType'] == l) &
                ((df_crop_details['season'] == "单季") |
                 (df_crop_details['season'] == "第一季"))
                ]['cost'].values[0] if df_crop_details[
                                           (df_crop_details['cropName'] == c) &
                                           (df_crop_details['cropLandType'] == l) &
                                           ((df_crop_details['season'] == "单季") |
                                            (df_crop_details['season'] == "第一季"))
                                           ]['cost'].values.size > 0 else 0
            for c in CropName
        },
        2: {
            c: df_crop_details[
                (df_crop_details['cropName'] == c) &
                (df_crop_details['cropLandType'] == l) &
                (df_crop_details['season'] == "第二季")
                ]['cost'].values[0] if df_crop_details[
                                           (df_crop_details['cropName'] == c) &
                                           (df_crop_details['cropLandType'] == l) &
                                           (df_crop_details['season'] == "第二季")
                                           ]['cost'].values.size > 0 else 0
            for c in CropName
        }
    }
    for l in LandType.values()
}


In [17]:
# 每种作物的总需求
crop_demand = {
    c: 0
    for c in CropName
}

# 这里需要另一张表
# 代码独立出来移到上面去了

for line in df_crop_planting.values:
    # 面积*该土地类型的亩产量    面积                      地块类型字典 地块类型     季节                  作物名称
    crop_demand[line[2]] += line[4] * unit_yield_lsc[LandType[line[0][0]]][SeasonDict[line[5]]][line[2]]


In [18]:
# 准备开搞
from pulp import LpMaximize, LpProblem, LpVariable, lpSum, value, PULP_CBC_CMD, LpContinuous, LpBinary
import pulp

In [19]:
model = LpProblem("Crop_Planting_Optimization_with_Specific_Rules", LpMaximize)

In [20]:

t = []
for y in years:
    for l in LandName:
        for s in SeasonNum:
            if l[0] in ["A", "B", "C"] and s == 1:
                for c in CropType["全粮食（除了水稻）"]:
                    t.append((c, l, y, s))
            if l[0] == "D":
                if s == 1:
                    for c in list(CropType["普通蔬菜"]) + ["水稻"]:
                        t.append((c, l, y, s))
                if s == 2:
                    for c in CropType["特殊蔬菜"]:
                        t.append((c, l, y, s))
            if l[0] == "E":
                if s == 1:
                    for c in list(CropType["普通蔬菜"]):
                        t.append((c, l, y, s))
                if s == 2:
                    for c in CropType["食用菌"]:
                        t.append((c, l, y, s))
            if l[0] == "F":
                for s in SeasonNum:
                    for c in CropType["普通蔬菜"]:
                        t.append((c, l, y, s))


# X

In [21]:
# 地块l在y年的s季的种植c的量
X = LpVariable.dicts("X", t,
                     lowBound=0,
                     cat=LpContinuous
                     )

In [22]:
# 地块l在y年的s季是否种植了c
Y = LpVariable.dicts("Y", t, cat=LpBinary)

In [23]:
tt = set(t)


def is_feasible(c, l, y, s):
    return (c, l, y, s) in tt

In [24]:
# 确保与X进行01约束
for c in CropName:
    for l in LandName:
        for y in years:
            for s in SeasonNum:
                # if 1:
                if is_feasible(c, l, y, s):
                    # 如果种植了作物，则种植面积大于0
                    model += X[c, l, y, s] <= 100 * Y[c, l, y, s], f"PlantingConstraint1_{c}_{l}_{y}_{s}"
                    # 如果未种植作物，则种植面积为0
                    model += X[c, l, y, s] >= 0.001 * Y[c, l, y, s], f"PlantingConstraint2_{c}_{l}_{y}_{s}"

min_area = 0.2
for c in CropName:
    for l in LandName:
        for y in years:
            for s in SeasonNum:
                if is_feasible(c, l, y, s):  # 最小面积约束和加强版01约束
                    model += X[c, l, y, s] <= LandArea[l] * Y[c, l, y, s], f"LandAreaConstraint_{c}_{l}_{y}_{s}"
                    model += X[c, l, y, s] >= min_area * (
                        1 if Y[c, l, y, s] else 0), f"MinAreaConstraint_{c}_{l}_{y}_{s}"

In [25]:
# 初始化总目标函数的表达式
total_profit = lpSum([])  # 空的lpSum用于初始化

# 累积每个作物、每个年份的利润和惩罚
for c in CropName:
    for y in years:
        # 计算利润部分
        profit_term = lpSum(
            X[c, l, y, s] * unit_profit_lsc[LandType[l[0]]][s][c]
            for l in LandName for s in SeasonNum if is_feasible(c, l, y, s)
        )

        # 惩罚超过需求的部分：将每个地块、每个季节的单位成本与种植量相乘
        penalty_term = lpSum(
            X[c, l, y, s] * unit_cost_lsc[LandType[l[0]]][s][c]
            for l in LandName for s in SeasonNum if is_feasible(c, l, y, s)
        ) - crop_demand[c] * lpSum(
            unit_cost_lsc[LandType[l[0]]][s][c]
            for l in LandName for s in SeasonNum if is_feasible(c, l, y, s)
        )

        # 累积到总目标函数中
        total_profit += profit_term - penalty_term

# 一次性将目标函数添加到模型中
model += total_profit, "total_profit"


In [27]:
# 条件2： 每年每季每块地的种植面积不能超过该地块的总面积
for l in LandName:
    for y in years:
        for s in SeasonNum:
            model += lpSum(X[c, l, y, s] for c in CropName if is_feasible(c, l, y, s)) <= LandArea[
                l], f"LandAreaConstraint_{l}_{y}_{s}"

In [28]:
# 条件3： 平旱地、梯田和山坡地每年适宜单季种植[粮食类作物（水稻除外）]。因为除了[粮食类作物（水稻除外）]以外的作物似乎已经被上面给约束了，所以大概不需要做限制了吧
for l in LandName:
    if l[0] in ["A", "B", "C"]:  # ["平旱地", "梯田", "山坡地"]
        for y in years:
            model += lpSum(
                Y[c, l, y, 2] for c in CropName if is_feasible(c, l, y, 2)) == 0, f"SingleSeasonConstraint1_{y}_{l}"



In [29]:
# 条件4： 水浇地每年可以单季种植水稻或两季种植蔬菜作物。
for l in LandName:
    if l[0] == "D":
        for y in years:
            for c in CropType["全蔬菜"]:
                if is_feasible(c, l, y, 2):
                    model += Y["水稻", l, y, 1] + Y[c, l, y, 2] <= 1, f"IrrigatedConstraint0_{l}_{y}_{c}"


In [30]:
# 条件10： 别种得太碎了，啥意思？ 每种作物不超过4块地吧。
for c in CropName:
    for y in years:
        for s in SeasonNum:
            model += lpSum(
                Y[c, l, y, s] for l in LandName if is_feasible(c, l, y, s)) <= 3, f"MaxCropTypeConstraint_{c}_{y}_{s}"

In [31]:
# 条件11： 每块地最大种植作物种类数3
for l in LandName:
    for y in years:
        for s in SeasonNum:
            model += lpSum(
                Y[c, l, y, s] for c in CropName if is_feasible(c, l, y, s)) <= 3, f"MaxLandConstraint_{l}_{y}_{s}"

In [32]:
# 条件12： 最小种植面积：0.2吧
for l in LandName:
    for y in years:
        for s in SeasonNum:
            for c in CropName:
                if is_feasible(c, l, y, s):
                    model += X[c, l, y, s] >= 0.2 * (
                        1 if X[c, l, y, s] else 0), f"MinCropAreaConstraint_{c}_{l}_{y}_{s}"

In [33]:
# 条件13 ： 最重要的，不能重复种植同一块地同一年同一季的同一作物
# 每种作物在同一地块（含大棚）都不能连续重茬种植

for l in LandName:
    for c in CropName:
        for y in years[1:]:  # 单季不能连年种植 同一年不能连续种植 跨年也不能连续种植
            if is_feasible(c, l, y - 1, 1) and is_feasible(c, l, y - 1, 2):
                model += Y[c, l, y - 1, 1] + Y[c, l, y - 1, 2] <= 1, f"RepeatPlantingConstraint_{c}_{l}_{y}"
                model += Y[c, l, y - 1, 2] + Y[c, l, y, 1] <= 1, f"RepeatPlantingConstraint1_{c}_{l}_{y}"
            if is_feasible(c, l, y - 1, 1) and is_feasible(c, l, y, 1):
                if l[0] in ["A", "B", "C"]:  # and c in CropType["全粮食"]:
                    model += Y[c, l, y - 1, 1] + Y[c, l, y, 1] <= 1, f"RepeatPlantingConstraint2_{c}_{l}_{y}"
                elif l[0] == "D" and c == "水稻":
                    model += Y[c, l, y - 1, 1] + Y[c, l, y, 1] <= 1, f"RepeatPlantingConstraint3_{c}_{l}_{y}"


In [34]:
# 条件14：从 2023 年开始，要求每个地块（含大棚） 在三年内至少种满一次豆类作物
for l in LandName:
    for y in years[2:]:  # 只需循环到倒数第三年，因为要考虑三年周期
        # 在 y-2 到 y+2 之间的三年内，至少种满一次豆类作物
        model += lpSum(X[c, l, y_r, s]
                       for c in CropType['豆类']
                       for y_r in range(y - 2, y + 1)
                       for s in SeasonNum if is_feasible(c, l, y_r, s)) >= LandArea[l], f"BeanConstraint_{l}_{y}"


In [35]:
%%time
model.solve(
    pulp.GUROBI_CMD(msg=True,
                    timeLimit=7200,
                    threads=20,
                    options=[("Method", 2), ("MIPGap", 0.0001)]))


CPU times: total: 78.1 ms
Wall time: 13.6 s


1

In [36]:
# 输出文件名，包含起始年份和结束年份
output_filename = f"planting_plan_1_1_{years[0]}-{years[-1]}.xlsx"

with pd.ExcelWriter(output_filename) as writer:
    for y in years:

        # 用于存储需要交换的DataFrame
        sheets_to_swap = {}

        for s in SeasonNum:
            # 创建一个空的 DataFrame，横轴为作物名称，纵轴为地块名称
            result_table = pd.DataFrame(columns=CropName, index=LandName)

            # 填充表格数据
            for l in LandName:
                for c in CropName:
                    # 获取变量 X[c, l, y, s] 的值
                    if is_feasible(c, l, y, s):
                        crop_value = value(X[c, l, y, s])
                        if crop_value is not None and crop_value > 0:
                            result_table.at[l, c] = crop_value  # 填入结果

            # 用 0 填充空值
            result_table.fillna(0, inplace=True)
            sheet_name = f"{y}_Season_第{s}季"
            result_table.to_excel(writer, sheet_name=sheet_name)

print(f"结果已保存到文件：{output_filename}")


结果已保存到文件：planting_plan_1_1_2024-2030.xlsx


In [37]:
# 四舍五入版
output_filename = f"planting_plan_1_1_{years[0]}-{years[-1]}-四舍五入版.xlsx"

with pd.ExcelWriter(output_filename) as writer:
    for y in years:
        # 用于存储需要交换的DataFrame
        sheets_to_swap = {}

        for s in SeasonNum:
            # 创建一个空的 DataFrame，横轴为作物名称，纵轴为地块名称
            result_table = pd.DataFrame(columns=CropName, index=LandName)

            # 填充表格数据
            for l in LandName:
                for c in CropName:
                    # 获取变量 X[c, l, y, s] 的值
                    if is_feasible(c, l, y, s):
                        crop_value = value(X[c, l, y, s])
                        if crop_value is not None and crop_value > 0:
                            result_table.at[l, c] = crop_value  # 填入结果

            # 用 0 填充空值
            result_table.fillna(0, inplace=True)

            # 对DataFrame中的所有数值进行四舍五入，保留两位小数
            result_table = result_table.round(2)

            sheet_name = f"{y}_Season_第{s}季"
            result_table.to_excel(writer, sheet_name=sheet_name)
